In [ ]:
%matplotlib notebook
import matplotlib.pyplot as plt

def plot_to_notebook(t, din, ns, dout=None):
    plt.figure()
    plt.subplot(1,1,1)
    plt.xlabel('Time')
    plt.grid()
    plt.plot(t[:ns]*1e6, din[:ns], 'y-', label='in sig')
    if dout is not None:
        plt.plot(t[:ns]*1e6, dout[:ns], 'g-', label='out sig')
    plt.legend()

In [ ]:
import numpy as np

T = 0.002
fs = 100e6
n = int(T * fs)
t =np.linspace(0, T, n, endpoint=False)
sample = 10000*np.sin(0.2e6*2*np.pi*t) + 1500*np.cos(46e6*2*np.pi*t) + 2000*np.sin(12e6*2*np.pi*t)
sample = sample.astype(np.int32)
print('# sample: ', len(sample))

plot_to_notebook(t, sample, 1000)

In [ ]:
from scipy.signal import lfilter

coffe = [-255,-260,312,-288,-144,153,616,1233,1963,2739,3474,4081,4481,4620,4481,4081,3474,2739,1963,1233,616,153,-144,-288,-312,-260,-255]

import time

stime = time.time()
sw_fir = lfilter(coffe, 70e3, sample)
etime = time.time()
sw_exec_time = etime - stime
print('Tot :', sw_exec_time)

plot_to_notebook(t, sample, 1000, dout=sw_fir)


In [ ]:
from pynq import Overlay

overlay = Overlay('/home/xilinx/jupyter_notebooks/pynq_overlay/fir_acc/fir_acc.bit')

In [ ]:
overlay?

In [ ]:
dma = overlay.filter.fir_dma

In [ ]:
from pynq import allocate
import numpy as np

in_buff = allocate(shape=(n,), dtype=np.int32)
out_buff = allocate(shape=(n,), dtype=np.int32)

np.copyto(in_buff, sample)

import time
stime = time.time()
dma.sendchannel.transfer(in_buff)
dma.recvchannel.transfer(out_buff)
dma.sendchannel.wait()
dma.recvchannel.wait()
etime = time.time()
hw_exec_time = etime - stime
print('Tot :', hw_exec_time)
print('Acc :', sw_exec_time / hw_exec_time)

plot_to_notebook(t, sample, 1000, dout=out_buff)

in_buff.close()
out_buff.close()

